# Neural Network 

> 1.Neural Network Benchmark model
<br>
> 2.use grid search to get the parameter for best neural network

In [1]:
import pandas as pd
import numpy as np 
import glob
from operator import itemgetter
from sklearn.metrics import *
from sklearn.neural_network import MLPRegressor
import dask.dataframe as dd
#import dask_ml.joblib
from sklearn.externals.joblib import parallel_backend
from dask.distributed import Client
from Error_Metrics import ErrorMetrics
from sklearn.model_selection import RandomizedSearchCV

In [7]:
df_train = pd.read_csv('blog_feedback_train.csv')
df_test = pd.read_csv('blog_feedback_test.csv')
X_train = df_train.loc[:,df_train.columns != '281']
y_train = df_train['281']
X_test = df_test.loc[:,df_test.columns != '281']
y_test = df_test['281']

In [8]:
def report(grid_scores, n_top=3):
    top_scores = sorted(grid_scores, key=itemgetter(1), reverse=True)[:n_top]
    for i, score in enumerate(top_scores):
        print("Model with rank: {0}".format(i + 1))
        print("Mean validation score: {0:.3f} (std: {1:.3f})".format(
              score.mean_validation_score,
              np.std(score.cv_validation_scores)))
        print("Parameters: {0}".format(score.parameters))
        print("")
    
mlp = MLPRegressor(hidden_layer_sizes=(50,), max_iter=10000,batch_size=600,
                    solver='sgd',  random_state=1,activation="logistic",learning_rate="constant")

mlp.fit(X_train, y_train)
    
    
print("Training set score: %f" % mlp.score(X_train, y_train))
print("Test set score: %f" % mlp.score(X_test, y_test))


Training set score: 0.001764
Test set score: 0.000428


In [9]:
error_metrics_nn = ErrorMetrics(X_train,y_train,X_test,y_test)
error_metrics_nn.cal_metric('neural network',mlp)

In [10]:
error_metrics_nn.error_metric

Model  mae_test  mae_train  mape_test  mape_train    r_test  \
0  neural network  9.157286  10.040854        inf         inf  0.000428   

    r_train  rmse_test  rmse_train  
0  0.001764  30.493361   37.672933

In [12]:
param_grid = { "alpha":[.1,.01,.01],
               "momentum":[.01,.05,0.1],
               "learning_rate_init":[.1,.01,.01]
}
mlp_grid= MLPRegressor(hidden_layer_sizes=(50,), max_iter=10000,batch_size=600,
                    solver='sgd',  random_state=1,activation="logistic",learning_rate="constant")

random_search = RandomizedSearchCV(mlp_grid, param_distributions= param_grid,n_iter = 8, cv=5)
random_search.fit(X_train.values, y_train.values)
    

RandomizedSearchCV(cv=5, error_score='raise',
          estimator=MLPRegressor(activation='logistic', alpha=0.0001, batch_size=600, beta_1=0.9,
       beta_2=0.999, early_stopping=False, epsilon=1e-08,
       hidden_layer_sizes=(50,), learning_rate='constant',
       learning_rate_init=0.001, max_iter=10000, momentum=0.9,
       nesterovs_momentum=True, power_t=0.5, random_state=1, shuffle=True,
       solver='sgd', tol=0.0001, validation_fraction=0.1, verbose=False,
       warm_start=False),
          fit_params=None, iid=True, n_iter=8, n_jobs=1,
          param_distributions={'alpha': [0.1, 0.01, 0.01], 'momentum': [0.01, 0.05, 0.1], 'learning_rate_init': [0.1, 0.01, 0.01]},
          pre_dispatch='2*n_jobs', random_state=None, refit=True,
          return_train_score='warn', scoring=None, verbose=0)

In [13]:
report(random_search.grid_scores_,10)
best = random_search.best_estimator_

print("Test set score of best nnet: %f" % best.score(X_test, y_test))
print("Best alpha: %f" % best.alpha)
print("Best momentum: %f" % best.momentum)
print("Best initial learning rate: %f" % best.learning_rate_init)

Model with rank: 1
Mean validation score: -0.031 (std: 0.024)
Parameters: {'momentum': 0.01, 'learning_rate_init': 0.1, 'alpha': 0.1}

Model with rank: 2
Mean validation score: -0.039 (std: 0.031)
Parameters: {'momentum': 0.05, 'learning_rate_init': 0.01, 'alpha': 0.01}

Model with rank: 3
Mean validation score: -0.039 (std: 0.031)
Parameters: {'momentum': 0.05, 'learning_rate_init': 0.01, 'alpha': 0.01}

Model with rank: 4
Mean validation score: -0.039 (std: 0.031)
Parameters: {'momentum': 0.05, 'learning_rate_init': 0.01, 'alpha': 0.01}

Model with rank: 5
Mean validation score: -0.040 (std: 0.033)
Parameters: {'momentum': 0.01, 'learning_rate_init': 0.01, 'alpha': 0.1}

Model with rank: 6
Mean validation score: -0.040 (std: 0.032)
Parameters: {'momentum': 0.01, 'learning_rate_init': 0.01, 'alpha': 0.01}

Model with rank: 7
Mean validation score: -0.047 (std: 0.037)
Parameters: {'momentum': 0.1, 'learning_rate_init': 0.01, 'alpha': 0.01}

Model with rank: 8
Mean validation score: -0.

/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_search.py:761: DeprecationWarning: The grid_scores_ attribute was deprecated in version 0.18 in favor of the more elaborate cv_results_ attribute. The grid_scores_ attribute will not be available from 0.20
  DeprecationWarning)


In [14]:
error_metrics_nn_opt = ErrorMetrics(X_train,y_train,X_test,y_test)
error_metrics_nn_opt.cal_metric('optimal neural network',best)
error_metrics_nn_opt.error_metric

Model   mae_test  mae_train  mape_test  mape_train  \
0  optimal neural network  11.615027  12.506906        inf         inf   

     r_test   r_train  rmse_test  rmse_train  
0 -0.012444 -0.001774  30.689073   37.739643

In [34]:
pd.concat([error_metrics_nn_opt.error_metric,error_metrics_nn.error_metric])

Model   mae_test  mae_train  mape_test  mape_train  \
0  optimal neural network   9.154931  10.899370        inf         inf   
0          neural network  10.046736  11.646153        inf         inf   

     r_test   r_train  rmse_test  rmse_train  
0  0.005573  0.002941  30.414787   37.650720  
0  0.002695  0.002315  30.458771   37.662533

tornado.application - ERROR - Exception in callback <bound method SystemMonitor.update of <SystemMonitor: cpu: 27 memory: 18 MB fds: 255>>
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/ioloop.py", line 1026, in _run
    return self.callback()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/system_monitor.py", line 71, in update
    read_bytes = (ioc.bytes_recv - last.bytes_recv) / (duration or 0.5)
AttributeError: 'NoneType' object has no attribute 'bytes_recv'--- Logging error ---
tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x11d350d90>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/ioloop.py", line 1026, in _run
    return self.callback()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/system_monitor.py", line 71, in update
    read_bytes = (io

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x1187748c8>, <tornado.concurrent.Future object at 0x12bed2f60>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 174, in read
    n_frames = yield stream.read_bytes(8)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 324, in read_bytes
    self._try_inline_read()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 709, in _try_inline_read
    self._check_closed()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 925, in _check_closed
    raise StreamClosedError(real_error=self.error)
tornado.iostream.StreamClosedError: Stream is closed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c01fe18>, <tornado.concurrent.Future object at 0x12bf00a90>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 174, in read
    n_frames = yield stream.read_bytes(8)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 324, in read_bytes
    self._try_inline_read()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 709, in _try_inline_read
    self._check_closed()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/iostream.py", line 925, in _check_closed
    raise StreamClosedError(real_error=self.error)
tornado.iostream.StreamClosedError: Stream is closed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12bfffbf8>, <tornado.concurrent.Future object at 0x12b597668>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 309, in connect
    **kwargs)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run


...

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c3ecd08>, <tornado.concurrent.Future object at 0x12bb35a58>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
    quiet_exceptions=EnvironmentError)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
tornado.gen.TimeoutError: Timeout

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/ioloop.py", line 605, in _run_callback
    ret = callback()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/sit

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c065400>, <tornado.concurrent.Future object at 0x10e2000b8>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
    quiet_exceptions=EnvironmentError)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 309, in connect
    **kwargs)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packa

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c301158>, <tornado.concurrent.Future object at 0x1188f3278>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
    quiet_exceptions=EnvironmentError)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 309, in connect
    **kwargs)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packa

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c301a60>, <tornado.concurrent.Future object at 0x119681198>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
    quiet_exceptions=EnvironmentError)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
tornado.gen.TimeoutError: Timeout

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/ioloop.py", line 605, in _run_callback
    ret = callback()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/sit

tornado.application - ERROR - Exception in callback functools.partial(<function wrap.<locals>.null_wrapper at 0x12c2380d0>, <tornado.concurrent.Future object at 0x135f7c208>)
Traceback (most recent call last):
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/core.py", line 185, in connect
    quiet_exceptions=EnvironmentError)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1055, in run
    value = future.result()
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/concurrent.py", line 238, in result
    raise_exc_info(self._exc_info)
  File "<string>", line 4, in raise_exc_info
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/tornado/gen.py", line 1063, in run
    yielded = self.gen.throw(*exc_info)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packages/distributed/comm/tcp.py", line 309, in connect
    **kwargs)
  File "/Users/xuchenlian/anaconda3/lib/python3.6/site-packa

In [17]:
best

MLPRegressor(activation='logistic', alpha=0.1, batch_size=600, beta_1=0.9,
       beta_2=0.999, early_stopping=False, epsilon=1e-08,
       hidden_layer_sizes=(50,), learning_rate='constant',
       learning_rate_init=0.1, max_iter=10000, momentum=0.01,
       nesterovs_momentum=True, power_t=0.5, random_state=1, shuffle=True,
       solver='sgd', tol=0.0001, validation_fraction=0.1, verbose=False,
       warm_start=False)